In [1]:
import numpy as np
import scipy as sp
import scipy.stats as spstats
import scipy.optimize as spopt

In [2]:
def generate_grid(sigma_s, sigma_b, mu_tot, grid_size=[60, 60]):
    grid = (
        mu_tot
      + (np.random.normal(size=grid_size[0]) * sigma_s)[:, np.newaxis]
      + (np.random.normal(size=grid_size[1]) * sigma_b)[np.newaxis, :]
      + np.random.normal(size=grid_size)
    )
    grid = 1 * (grid > 0)
    return grid

In [3]:
def grid_statistics(grid):
    return np.array([
        grid.var(axis=0, ddof=1).mean(),
        grid.var(axis=1, ddof=1).mean(),
        grid.mean()
    ])

In [4]:
def integrate(f, domain=[-20, 20], num_samples=10_000):
    xs = np.linspace(*domain, num_samples)
    ys = f(xs)
    dx = (domain[1] - domain[0]) / num_samples
    return (ys * dx).sum()

In [5]:
def expected_variance(sigma, mu):
    integrand = lambda x: spstats.norm.cdf(x) * (1 - spstats.norm.cdf(x)) * spstats.norm.pdf((x - mu) / sigma) / sigma
    return integrate(integrand)

In [6]:
def L(parameters, sample_statistics):
    sigma_s, sigma_b, mu_tot = parameters

    expected_var_row = expected_variance(sigma=sigma_b / np.sqrt(1 + sigma_s ** 2), mu=mu_tot / np.sqrt(1 + sigma_s ** 2))
    expected_var_column = expected_variance(sigma=sigma_s / np.sqrt(1 + sigma_b ** 2), mu=mu_tot / np.sqrt(1 + sigma_b ** 2))
    expected_mean_tot = spstats.norm.cdf(mu_tot / np.sqrt(1 + sigma_s ** 2 + sigma_b ** 2))

    sample_var_row, sample_var_column, sample_mean_tot = sample_statistics
    
    return np.log(
        (np.array([
            expected_var_row - sample_var_row,
            expected_var_column - sample_var_column,
            expected_mean_tot - sample_mean_tot,
        ]) ** 2.).sum()
    )

In [7]:
grid = generate_grid(sigma_s=2.4, sigma_b=0.6, mu_tot=-1.5)
sample_statistics = grid_statistics(grid)

In [8]:
inferred_parameters = spopt.minimize(
    lambda parameters: L(parameters, sample_statistics),
    x0=np.ones(3)
).x

inferred_parameters

array([ 2.29071775,  0.57796239, -1.57644119])